In [1]:
import xarray as xr
import hvplot.xarray
import cartopy.crs as ccrs
import geoviews


url = 'http://thredds.secoora.org/thredds/dodsC/SECOORA_NCSU_CNAPS.nc'

ds = xr.open_dataset(url)

### xarray: in-memory netCDF-like file, or 'pandas for netCDF'

Allows you to work with netCDF data using common Python syntax and functions for handling array data.  

Use labels (similar to Pandas) to identify, select, manipulate variables. 

First, let's inspect an xarray dataset we just loaded:

In [2]:
ds

<xarray.Dataset>
Dimensions:      (eta_psi: 481, eta_rho: 482, eta_u: 482, eta_v: 481, s_rho: 36, s_w: 37, time: 5602, xi_psi: 401, xi_rho: 402, xi_u: 401, xi_v: 402)
Coordinates:
    lat_psi      (eta_psi, xi_psi) float64 ...
    lat_rho      (eta_rho, xi_rho) float64 ...
    lat_u        (eta_u, xi_u) float64 ...
    lat_v        (eta_v, xi_v) float64 ...
    lon_psi      (eta_psi, xi_psi) float64 ...
    lon_rho      (eta_rho, xi_rho) float64 ...
    lon_u        (eta_u, xi_u) float64 ...
    lon_v        (eta_v, xi_v) float64 ...
  * s_rho        (s_rho) float64 -0.9861 -0.9583 -0.9306 -0.9028 -0.875 ...
  * s_w          (s_w) float64 -1.0 -0.9722 -0.9444 -0.9167 -0.8889 -0.8611 ...
  * time         (time) datetime64[ns] 2016-05-02 2016-05-02T03:00:00 ...
Dimensions without coordinates: eta_psi, eta_rho, eta_u, eta_v, xi_psi, xi_rho, xi_u, xi_v
Data variables:
    Cs_r         (s_rho) float64 ...
    Cs_w         (s_w) float64 ...
    angle        (eta_rho, xi_rho) float64 ...
    

The .info() command will give a more expanded summary of the dataset (unpack and display variable attribution details, etc)

In [3]:
ds.info()

xarray.Dataset {
dimensions:
	eta_psi = 481 ;
	eta_rho = 482 ;
	eta_u = 482 ;
	eta_v = 481 ;
	s_rho = 36 ;
	s_w = 37 ;
	time = 5602 ;
	xi_psi = 401 ;
	xi_rho = 402 ;
	xi_u = 401 ;
	xi_v = 402 ;

variables:
	float64 Cs_r(s_rho) ;
		Cs_r:long_name = S-coordinate stretching curves at RHO-points ;
		Cs_r:valid_min = -1.0 ;
		Cs_r:valid_max = 0.0 ;
		Cs_r:field = Cs_r, scalar ;
		Cs_r:_ChunkSizes = 36 ;
	float64 Cs_w(s_w) ;
		Cs_w:long_name = S-coordinate stretching curves at W-points ;
		Cs_w:valid_min = -1.0 ;
		Cs_w:valid_max = 0.0 ;
		Cs_w:field = Cs_w, scalar ;
		Cs_w:_ChunkSizes = 37 ;
	float64 angle(eta_rho, xi_rho) ;
		angle:units = radians ;
		angle:long_name = angle between XI-axis and EAST ;
		angle:field = angle, scalar ;
		angle:_ChunkSizes = [482 402] ;
	float64 f(eta_rho, xi_rho) ;
		f:units = second-1 ;
		f:long_name = Coriolis parameter at RHO-points ;
		f:field = coriolis, scalar ;
		f:_ChunkSizes = [482 402] ;
	float64 h(eta_rho, xi_rho) ;
		h:time = time ;
		h:field = ba

### Plotting with xarray:

Let's use only the surface temperature (-1 on ROMS models).

Here, we select the `temp` variable, subsetting all values in the time dimension, -1 for sigma level dimension `s_rho`, and all values of the other two dimensions `eta_rho` and `xi_rho`.  Time variable is structured like this:

```
float32 temp(time, s_rho, eta_rho, xi_rho) ;
		temp:standard_name = sea_water_potential_temperature ;
		temp:field = temperature, scalar, series ;
		temp:units = degree_Celsius ;
		temp:time = time ;
		temp:long_name = Potential Temperature ;
		temp:_ChunkSizes = [  8  36 482 402] ;
```




In [4]:
surface_temp = ds['temp'][:, -1, ...].squeeze()

You can also use '.' dot selectors in xarray as you can in pandas.  The assigment below is equivalent to the one above:

In [5]:
surface_temp = ds.temp[:, -1, ...].squeeze()

Next, we create a simple plot with a timeslider using the hvplot library:

In [6]:
surface_temp.hvplot.quadmesh(
    groupby='time',
    x='lon_rho',
    y='lat_rho',
    projection=ccrs.PlateCarree(),
    width=600, height=540,
    cmap='viridis',
    rasterize=True,
    dynamic=True,
) * geoviews.feature.land

:DynamicMap   [time]
   :Overlay
      .Image.I :Image   [lon_rho,lat_rho]   (temp)
      .Land.I  :Feature   [Longitude,Latitude]